In [0]:
%sql
create catalog oleksii_dubynskyi_nyc_catalog
managed location 's3://odubynskyi-hw-7/'

In [0]:
%sql
GRANT ALL PRIVILEGES ON CATALOG `oleksii_dubynskyi_nyc_catalog` TO `deniskulemza1@gmail.com`;

In [0]:
%sql
CREATE SCHEMA IF NOT EXISTS oleksii_dubynskyi_nyc_catalog.trips_schema
COMMENT 'Schema для даних yellow/green trips';

In [0]:
%python
# 2 завдання
from pyspark.sql import functions as F

# Параметри
catalog         = "oleksii_dubynskyi_nyc_catalog"
schema          = "trips_schema"
raw_path        = "s3a://robot-dreams-source-data/home-work-1-unified/nyc_taxi/"
lookup_path     = raw_path + "taxi_zone_lookup.csv"           # <- тут лежить CSV з зонами
processed_table = f"{catalog}.{schema}.processed_trips"

# Зчитую Parquet‑файли з поїздками
df_raw = (
    spark.read
         .format("parquet")
         .option("recursiveFileLookup", "true")
         .option("ignoreCorruptFiles", "true")
         .load(raw_path)
)

# Додаю колонку taxi_type (yellow/green) за шляхом
df_typed = (
    df_raw
      .withColumn("file_path", F.input_file_name())
      .withColumn("taxi_type",
         F.when(F.col("file_path").contains("yellow"), "yellow")
          .when(F.col("file_path").contains("green"),  "green")
          .otherwise("unknown")
      )
      .drop("file_path")
)

# Обчислюю duration_min в хвилинах, округлюю до 2 знаків
df_duration = df_typed.withColumn(
    "duration_min",
    F.round(
      (F.unix_timestamp("tpep_dropoff_datetime")
        - F.unix_timestamp("tpep_pickup_datetime"))/60
      , 2
    )
)

# Фільтрую аномальні поїздки
df_filtered = df_duration.filter(
    (F.col("trip_distance") >= 0.1) &
    (F.col("fare_amount")   >= 2  ) &
    (F.col("duration_min")  >= 1  )
)

# Додаю часові ознаки
df_enriched = (
    df_filtered
      .withColumn("pickup_hour",        F.hour("tpep_pickup_datetime"))
      .withColumn("pickup_day_of_week", F.date_format("tpep_pickup_datetime","EEEE"))
)

# Зчитую lookup‑таблицю зон з CSV на S3
zones = (
    spark.read
         .option("header", True)
         .option("inferSchema", True)
         .csv(lookup_path)
)

# Готую два DataFrame для JOIN
zones_pu = zones.select(
                F.col("LocationID").alias("PULocationID"),
                F.col("Zone").alias("pickup_zone")
            )
zones_do = zones.select(
                F.col("LocationID").alias("DOLocationID"),
                F.col("Zone").alias("dropoff_zone")
            )

# З’єдную все разом
df_final = (
    df_enriched
      .join(zones_pu,
            df_enriched.PULocationID == zones_pu.PULocationID,
            "left")
      .join(zones_do,
            df_enriched.DOLocationID == zones_do.DOLocationID,
            "left")
      .select(
         "VendorID",
         "passenger_count",
         "trip_distance",
         "fare_amount",
         "tip_amount",
         "total_amount",
         "tpep_pickup_datetime",
         "tpep_dropoff_datetime",
         "duration_min",
         "pickup_hour",
         "pickup_day_of_week",
         "taxi_type",
         "pickup_zone",
         "dropoff_zone"
      )
)

# Записую результат у Delta‑таблицю в Unity Catalog
(df_final
   .write
   .format("delta")
   .mode("overwrite")
   .saveAsTable(processed_table)
)

# І, нарешті, виводжу DataFrame для перевірки
display(df_final)

VendorID passenger_count trip_distance fare_amount tip_amount total_amount tpep_pickup_datetime tpep_dropoff_datetime duration_min pickup_hour pickup_day_of_week taxi_type pickup_zone dropoff_zone 1 1 1.5 7.0 0.0 8.0 2014-10-01T00:53:11 2014-10-01T01:00:34 7.38 0 Wednesday yellow Meatpacking/West Village West Meatpacking/West Village West 1 1 0.7 5.0 1.5 7.5 2014-10-01T00:12:41 2014-10-01T00:16:20 3.65 0 Wednesday yellow Lower East Side Greenwich Village South 1 1 2.9 12.0 2.0 15.0 2014-10-01T00:21:14 2014-10-01T00:34:21 13.12 0 Wednesday yellow Little Italy/NoLiTa Brooklyn Heights 1 1 2.6 10.0 2.75 13.75 2014-10-01T00:46:15 2014-10-01T00:55:52 9.62 0 Wednesday yellow Lower East Side East Chelsea 2 1 19.79 53.5 10.8 65.3 2014-10-01T00:32:07 2014-10-01T01:03:53 31.77 0 Wednesday yellow JFK Airport Windsor Terrace 1 1 1.7 8.5 1.9 11.4 2014-10-01T00:06:27 2014-10-01T00:15:35 9.13 0 Wednesday yellow Hudson Sq East Village 1 1 1.1 6.0 0.0 7.0 2014-10-01T00:24:07 2014-10-01T00:29:19 5.2 0 Wednesday yellow Greenwich Village North Little Italy/NoLiTa 1 2 7.1 27.5 5.7 34.2 2014-10-01T00:04:29 2014-10-01T00:41:58 37.48 0 Wednesday yellow Flatiron Jackson Heights 1 1 2.7 10.5 0.0 11.5 2014-10-01T00:54:46 2014-10-01T01:04:58 10.2 0 Wednesday yellow West Chelsea/Hudson Yards Midtown East 1 1 1.9 8.5 0.0 9.5 2014-10-01T00:06:04 2014-10-01T00:13:55 7.85 0 Wednesday yellow Midtown East Yorkville West 1 1 2.8 11.0 2.4 14.4 2014-10-01T00:25:16 2014-10-01T00:35:54 10.63 0 Wednesday yellow Lincoln Square East Morningside Heights 1 1 13.6 43.0 0.0 44.0 2014-10-01T00:38:24 2014-10-01T01:21:58 43.57 0 Wednesday yellow Morningside Heights Bushwick North 2 1 2.47 9.5 0.0 10.5 2014-10-01T00:27:45 2014-10-01T00:36:33 8.8 0 Wednesday yellow Park Slope Crown Heights North 1 1 2.3 9.5 2.0 12.5 2014-10-01T00:00:45 2014-10-01T00:11:16 10.52 0 Wednesday yellow Flatiron Sutton Place/Turtle Bay North 1 1 1.0 5.5 1.6 8.1 2014-10-01T00:24:21 2014-10-01T00:28:56 4.58 0 Wednesday yellow Union Sq East Village 1 1 1.0 6.0 1.0 8.0 2014-10-01T00:30:37 2014-10-01T00:36:35 5.97 0 Wednesday yellow East Village Union Sq 1 2 1.5 7.5 1.0 9.5 2014-10-01T00:55:56 2014-10-01T01:03:47 7.85 0 Wednesday yellow Midtown North Murray Hill 1 1 1.2 7.5 2.12 10.62 2014-10-01T00:05:40 2014-10-01T00:14:46 9.1 0 Wednesday yellow Penn Station/Madison Sq West Midtown East 1 1 2.3 9.0 2.5 12.5 2014-10-01T00:24:45 2014-10-01T00:32:55 8.17 0 Wednesday yellow Midtown East Flatiron 1 1 3.3 11.5 2.5 15.0 2014-10-01T00:44:04 2014-10-01T00:54:11 10.12 0 Wednesday yellow Midtown South Upper East Side North 1 4 0.5 4.0 0.0 5.0 2014-10-01T00:06:03 2014-10-01T00:08:44 2.68 0 Wednesday yellow Upper East Side South Upper East Side North 1 2 1.0 5.0 0.0 6.0 2014-10-01T00:21:03 2014-10-01T00:24:29 3.43 0 Wednesday yellow Upper East Side South Central Park 1 2 1.6 8.0 1.8 10.8 2014-10-01T00:40:47 2014-10-01T00:48:40 7.88 0 Wednesday yellow Flatiron Meatpacking/West Village West 2 1 3.42 13.0 2.0 16.0 2014-10-01T00:50:33 2014-10-01T01:03:38 13.08 0 Wednesday yellow Lincoln Square East West Village 1 1 3.1 11.0 2.4 14.4 2014-10-01T00:03:00 2014-10-01T00:13:26 10.43 0 Wednesday yellow Lincoln Square East Kips Bay 1 1 2.4 9.5 2.0 12.5 2014-10-01T00:13:03 2014-10-01T00:22:03 9.0 0 Wednesday yellow Midtown Center Lincoln Square East 1 1 0.9 5.0 0.6 6.6 2014-10-01T00:01:04 2014-10-01T00:04:02 2.97 0 Wednesday yellow Union Sq Penn Station/Madison Sq West 1 1 1.3 7.0 2.4 10.4 2014-10-01T00:39:15 2014-10-01T00:45:39 6.4 0 Wednesday yellow Greenwich Village North Kips Bay 1 1 2.7 11.0 3.6 15.6 2014-10-01T00:19:01 2014-10-01T00:29:34 10.55 0 Wednesday yellow Clinton East Upper West Side North 1 1 0.5 4.5 0.0 5.5 2014-10-01T00:40:22 2014-10-01T00:44:23 4.02 0 Wednesday yellow Lincoln Square East Midtown North 2 1 4.9 62.0 18.6 81.1 2014-10-01T00:22:53 2014-10-01T00:35:42 12.82 0 Wednesday yellow Clinton East Outside of NYC 2 1 5.75 17.0 4.38 22.38 2014-10-01T00:00:55 2014-10-01T00:11:23 10.47 0 Wednesday yellow Upper Wes

In [0]:
%python
# 3 завдання
from pyspark.sql import functions as F

# Параметри
catalog            = "oleksii_dubynskyi_nyc_catalog"
schema             = "trips_schema"
processed_table    = f"{catalog}.{schema}.processed_trips"
output_table       = f"{catalog}.{schema}.zone_summary"

# Завантажую оброблені поїздки
df = spark.table(processed_table)

# Роблю агрегацію по pickup_zone та обчислюю метрики
zone_summary = (
    df.groupBy("pickup_zone")
      .agg(
         F.count("*").alias("total_trips"),                                      # загальна кількість поїздок
         F.round(F.avg("trip_distance"), 2).alias("avg_trip_distance"),           # середня відстань
         F.round(F.avg("total_amount"), 2).alias("avg_total_amount"),             # середній дохід
         F.round(F.avg("tip_amount"), 2).alias("avg_tip_amount"),                 # середній чайові
         F.round(
             100 * F.sum(F.when(F.col("taxi_type")=="yellow",1).otherwise(0))
                   / F.count("*")
           , 2
         ).alias("yellow_share_pct"),                                             # % жовтих таксі
         F.round(
             100 * F.sum(F.when(F.col("taxi_type")=="green",1).otherwise(0))
                   / F.count("*")
           , 2
         ).alias("green_share_pct"),                                              # % зелених таксі
         F.round(F.max("trip_distance"), 2).alias("max_trip_distance"),           # макс. відстань
         F.round(F.min("tip_amount"), 2).alias("min_tip_amount"),                 # мін. чайові
         F.round(F.sum("total_amount"), 2).alias("total_amount_all_trips")        # сумарний дохід
      )
)

# Записую результат як Delta‑таблицю в Unity Catalog
(zone_summary
   .write
   .format("delta")
   .mode("overwrite")
   .saveAsTable(output_table)
)

# Виводжу збережену таблицю для перевірки
display(spark.table(output_table))

pickup_zone total_trips avg_trip_distance avg_total_amount avg_tip_amount yellow_share_pct green_share_pct max_trip_distance min_tip_amount total_amount_all_trips Homecrest 12564 5.4 24.68 1.43 100.0 0.0 126.5 0.0 310064.7 Governor's Island/Ellis Island/Liberty Island 1867 3.9 18.74 1.99 100.0 0.0 29.1 0.0 34990.81 Corona 31674 13.9 34.84 3.07 100.0 0.0 250984.47 0.0 1103394.52 Bensonhurst West 13792 31.85 27.82 1.47 100.0 0.0 350696.98 0.0 383630.65 Westerleigh 601 8.39 41.97 3.37 100.0 0.0 90.06 0.0 25222.48 Newark Airport 5356 9.42 79.84 8.15 100.0 0.0 202.9 0.0 427645.32 Douglaston 3276 9.99 41.84 2.56 100.0 0.0 92.0 0.0 137077.75 Charleston/Tottenville 1520 29.43 90.9 1.92 100.0 0.0 103.0 0.0 138173.79 East Concourse/Concourse Village 35916 9.27 19.71 0.93 100.0 0.0 130074.91 0.0 707993.6 Pelham Parkway 9879 5.78 25.23 1.19 100.0 0.0 104.15 0.0 249290.73 Mount Hope 17475 12.05 22.38 0.92 100.0 0.0 98782.5 0.0 391023.27 Marble Hill 8259 4.43 19.1 0.85 100.0 0.0 32.69 0.0 157717.94 Rego Park 70131 5.72 24.61 2.01 100.0 0.0 46532.54 0.0 1726197.52 Upper East Side South 28756454 4.96 12.72 1.37 100.0 0.0 1.2E7 -0.84 3.6567874473E8 Dyker Heights 7581 5.95 26.14 1.76 100.0 0.0 60.1 0.0 198205.14 Heartland Village/Todt Hill 845 10.67 44.03 2.1 100.0 0.0 145.1 0.0 37201.37 Kew Gardens Hills 18556 9.9 26.05 1.54 100.0 0.0 68704.94 0.0 483344.4 Rikers Island 477 4.03 20.08 2.21 100.0 0.0 48.94 0.0 9576.84 Jackson Heights 403558 3.85 16.13 0.96 100.0 0.0 106647.2 0.0 6507779.95 Bayside 5850 17.03 31.39 1.84 100.0 0.0 46826.21 0.0 183634.28 Yorkville West 13157794 5.72 13.98 1.57 100.0 0.0 1.46800001E7 0.0 1.8391249504E8 TriBeCa/Civic Center 13530916 10.95 16.67 1.91 100.0 0.0 1.24273318E7 0.0 2.2555922809E8 Highbridge 25478 6.98 22.33 1.28 100.0 0.0 33249.83 0.0 568833.29 Stuy Town/Peter Cooper Village 2159027 10.69 14.37 1.62 100.0 0.0 8000040.0 0.0 3.102749635E7 Flushing Meadows-Corona Park 87222 10.92 55.85 6.25 100.0 0.0 116348.45 0.0 4871324.73 Bushwick South 323593 4.2 16.21 1.56 100.0 0.0 127475.27 -0.82 5245734.48 Riverdale/North Riverdale/Fieldston 8159 7.81 31.17 1.86 100.0 0.0 57.41 0.0 254323.14 Windsor Terrace 34368 6.57 21.0 2.15 100.0 0.0 37523.74 0.0 721762.55 Old Astoria 464728 29.64 15.62 1.35 100.0 0.0 1.18000012E7 0.0 7260977.47 Clinton Hill 345286 6.31 15.76 1.57 100.0 0.0 250051.0 0.0 5442786.6 Ocean Hill 27457 7.83 24.26 1.37 100.0 0.0 48649.75 0.0 666026.19 West Concourse 103736 5.0 17.93 1.17 100.0 0.0 42022.4 0.0 1859937.71 Stuyvesant Heights 118505 4.62 17.72 1.44 100.0 0.0 65093.13 0.0 2099979.03 Freshkills Park 168 19.6 71.81 2.8 100.0 0.0 122.6 0.0 12063.39 Broad Channel 195 9.16 39.17 2.65 100.0 0.0 104.33 0.0 7638.46 Upper West Side North 13497189 6.98 13.84 1.53 100.0 0.0 1.620037E7 0.0 1.8673958629E8 Mariners Harbor 1078 10.78 47.48 3.31 100.0 0.0 156.17 0.0 51183.11 East Harlem South 4687490 3.41 14.04 1.28 100.0 0.0 833180.0 -0.07 6.580342581E7 Kensington 41345 4.74 20.75 1.8 100.0 0.0 5156.7 0.0 857979.19 Springfield Gardens North 14065 25.04 35.48 1.1 100.0 0.0 49267.74 0.0 499020.1 Oakland Gardens 3057 129.87 33.84 2.47 100.0 0.0 350814.14 0.0 103434.33 Crown Heights North 240588 5.97 18.44 1.63 100.0 0.0 144735.58 0.0 4437348.46 Longwood 8258 7.94 24.63 0.98 100.0 0.0 10973.55 0.0 203370.31 Hudson Sq 4385362 6.59 15.78 1.91 100.0 0.0 1.46645031E7 0.0 6.920969822E7 Lenox Hill East 12822397 7.49 14.91 1.63 100.0 0.0 1.53318E7 -2.75 1.9122955988E8 Flushing 43685 7.32 23.38 1.45 100.0 0.0 69058.79 0.0 1021404.68 Norwood 12894 14.33 27.91 1.19 100.0 0.0 99521.33 0.0 359848.26 Upper East Side North 25942621 3.57 13.28 1.47 100.0 0.0 1.18000052E7 -4.42 3.445298354E8 Columbia Street 45124 4.96 18.81 2.2 100.0 0.0 31751.2 0.0 848802.52 UN/Turtle Bay South 9969258 4.18 15.62 1.75 100.0 0.0 6710318.0 0.0 1.5576833498E8 Prospect Park 43043 7.59 17.86 1.76 100.0 0.0 86205.0 0.0 768915.91 Starrett City 8338 76.3 37.17 1.4 100.0 0.0 349987.05 0.0 309920.82 East Elmhurst 391847 10.06 47.28 5.77 100.0 0.0 1752

In [0]:
%python
# 4 завдання
from pyspark.sql import functions as F

# Параметри
catalog                 = "oleksii_dubynskyi_nyc_catalog"
schema                  = "trips_schema"
processed_table         = f"{catalog}.{schema}.processed_trips"
output_table            = f"{catalog}.{schema}.zone_days_summary"

# Завантажую оброблені поїздки
df = spark.table(processed_table)

# Роблю агрегацію по pickup_day_of_week та pickup_zone
zone_days_summary = (
    df.groupBy("pickup_day_of_week", "pickup_zone")
      .agg(
         F.count("*").alias("total_trips_per_day"),                             # кількість поїздок за день
         F.round(F.avg("duration_min"), 2).alias("avg_duration_min"),           # середня тривалість поїздки
         F.round(
             100 * F.sum(F.when(F.col("fare_amount") > 30, 1).otherwise(0))
                   / F.count("*")
           , 2
         ).alias("high_fare_share_pct")                                         # % поїздок із тарифом > $30
      )
)

# Записую результат як Delta‑таблицю в Unity Catalog
(zone_days_summary
   .write
   .format("delta")
   .mode("overwrite")
   .saveAsTable(output_table)
)

# Виводжу збережену таблицю для перевірки
display(spark.table(output_table))

pickup_day_of_week pickup_zone total_trips_per_day avg_duration_min high_fare_share_pct Friday Bensonhurst West 2101 27.44 31.75 Saturday Columbia Street 7780 15.77 6.52 Sunday East Flatbush/Remsen Village 2848 20.82 18.19 Monday Jamaica Bay 163 24.05 44.17 Thursday SoHo 907007 17.08 3.5 Thursday Red Hook 7816 25.71 23.14 Friday Upper East Side North 4012316 15.94 1.8 Saturday Baisley Park 17319 42.5 87.8 Saturday Queensboro Hill 1225 19.03 13.96 Saturday Springfield Gardens North 1477 25.34 41.77 Sunday Garment District 1609831 15.29 5.78 Sunday Lincoln Square West 976134 12.2 3.23 Sunday Newark Airport 956 23.5 76.05 Monday Melrose South 5429 17.69 11.92 Tuesday Midtown South 2496480 14.96 3.89 Tuesday Crown Heights North 23096 18.47 13.84 Tuesday Briarwood/Jamaica Hills 7081 27.78 58.66 Tuesday Bronx Park 297 26.86 36.03 Tuesday Bloomfield/Emerson Hill 413 45.85 81.36 Sunday South Beach/Dongan Hills 64 25.62 37.5 Wednesday Murray Hill-Queens 961 26.27 39.85 Wednesday Pelham Parkway 1423 22.33 24.6 Thursday Douglaston 498 26.32 55.02 Friday Parkchester 2057 24.46 30.29 Friday South Jamaica 8862 45.98 86.57 Friday Van Cortlandt Village 1635 21.92 26.24 Friday Flushing Meadows-Corona Park 11982 893.38 76.22 Saturday Midtown East 2774902 18.14 3.41 Saturday Springfield Gardens South 5005 39.46 78.46 Saturday North Corona 5052 14.96 7.58 Monday Bushwick South 27378 15.51 7.39 Friday Eltingville/Annadale/Prince's Bay 34 44.84 70.59 Saturday Greenwich Village North 1920190 14.8 2.42 Sunday University Heights/Morris Heights 3362 16.82 16.39 Tuesday Bath Beach 723 33.18 42.88 Tuesday College Point 1012 24.04 42.59 Thursday Jamaica Bay 229 25.85 35.81 Wednesday East Harlem South 676726 14.12 2.99 Wednesday Bedford 29828 15.51 6.34 Wednesday Mount Hope 2341 22.7 20.76 Wednesday Heartland Village/Todt Hill 149 28.37 36.24 Thursday Briarwood/Jamaica Hills 7251 30.22 58.16 Thursday Parkchester 1904 25.57 32.51 Saturday Lenox Hill West 2623542 12.54 1.68 Saturday Bedford Park 1928 17.84 18.57 Sunday Mott Haven/Port Morris 21650 16.18 7.02 Monday Greenwich Village South 1088791 13.73 2.72 Monday East Elmhurst 61427 28.25 56.99 Monday Roosevelt Island 5048 18.25 11.17 Monday Van Nest/Morris Park 2350 21.49 21.45 Monday Williamsbridge/Olinville 1965 28.02 46.51 Thursday Saint Michaels Cemetery/Woodside 1803 21.78 27.12 Friday Marine Park/Mill Basin 1597 28.5 35.63 Saturday TriBeCa/Civic Center 1961576 16.04 3.42 Sunday Clinton West 1153365 14.5 5.81 Sunday Saint Albans 1433 26.34 52.83 Tuesday Carroll Gardens 58565 17.21 7.41 Tuesday SoHo 832079 28.55 2.96 Tuesday Woodside 47951 16.62 9.13 Wednesday New Dorp/Midland Beach 43 24.38 44.19 Thursday Murray Hill 3800425 15.19 4.12 Thursday Yorkville East 1359522 13.78 2.2 Thursday Bushwick South 32994 15.44 6.6 Thursday Rosedale 1286 36.5 59.72 Thursday Queens Village 1724 28.29 49.13 Friday SoHo 953145 17.16 3.51 Friday Westerleigh 79 32.64 37.97 Saturday Stuy Town/Peter Cooper Village 413348 13.38 2.33 Saturday West Farms/Bronx River 1317 19.6 27.03 Saturday Melrose South 7378 16.4 7.2 Monday Astoria 152109 16.79 4.26 Monday Woodlawn/Wakefield 1047 25.79 45.27 Monday Schuylerville/Edgewater Park 1119 25.32 38.61 Wednesday Howard Beach 1389 32.53 56.95 Thursday Chinatown 229872 19.32 5.92 Friday Central Park 1537423 15.9 2.69 Friday Fordham South 993 21.55 21.15 Friday Green-Wood Cemetery 249 14.51 8.84 Sunday Woodlawn/Wakefield 1474 20.45 29.38 Monday West Chelsea/Hudson Yards 1375940 29.14 2.68 Monday Woodhaven 1924 23.12 32.59 Tuesday DUMBO/Vinegar Hill 47719 17.47 5.25 Tuesday West Farms/Bronx River 1138 26.34 35.5 Wednesday Cypress Hills 1513 28.31 42.3 Tuesday Saint George/New Brighton 210 30.43 32.86 Wednesday Hudson Sq 687250 15.96 4.18 Wednesday Norwood 1969 24.17 29.76 Thursday Bedford 31850 15.51 6.77 Thursday Financial District North 901934 21.55 10.19 Thursday Rego Park 9471 19.12 20.95 Thursday Queensbridge/Ravenswood 33440 15.59 5.3 Friday Meatpacking/West Village West 1436866 23.